# 2D to 3D LSTM

This is the first approach to try to estimate 3D points coordinates from 2D keypoints extracted with Openpose. Here I will build a simple LSTM to perform the task over the Panoptic Studio dataset.

First, let's import all the necessary libraries.

In [2]:
# Pytorch utilities
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader
# Plotting utilities
%matplotlib widget
import matplotlib
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from IPython.display import HTML
import matplotlib.animation as animation
from torch.utils.tensorboard import SummaryWriter
from timeit import default_timer as timer
import pyprind

# Directory and file utilities
from os import listdir
from os.path import isfile, isdir, join
import json

## Data acquisition
Now I will define some functions in order to parse and organise the data, and later convert it to pytorch tensors.

The data is structured as follows: in the dataset directory there are several folders, each folder corresponds to a recording; each of these folders contains a folder with the audio, folders with face, hands and body keypoints estimations for each frame, and a folder with the video recorded from different views.

In this first approach I will be using the keypoints estimations. Every keypoint folder (face, hands or body) is organized the same way: it contains a json per frame of the video, which includes the 3D keypoints estimation.

The function `get_keypoints` will go through each folder in the dataset directory and retrieve the face keypoints, the hands keypoints and the body keypoints. It will separate them into input (2D coordinates per joint per frame) and grountruth (third coordinate to estimate for each input 2D keypoint). 
The input will be of shape $([n videos, seq len, input size])$, where *seq_len* = number of frames, and *input_size* = face + hands + body keypoints, that is (70+(21+21)+26)x2 -multiplied by 2 because there are x and y coordinates-. The groundtruth (label) data will be of the same shape, except that the last dimension size will not be multiplied by 2 (there's only one coordinate to estimate).  

In [3]:
def get_keypoints(data_path):
    dataset = []
    groundtruth = []
    # Look over just the folders inside the directory
    just_folders = filter(lambda x: isdir(join(data_path, x)), listdir(data_path))
    for p in list(map(lambda x: join(data_path, x), just_folders)): 
        # Gets 2 list of n_frames lists, one for the 2D coordinates and one for the third coordinate.
        # Each list of the n_frames lists contains, either the (x and y) or the z of each keypoint for the face(first line), hands(second), body(third).
        # e.g. the first line will result in [[x1,y1,x2,y2...x70,y70]sub1...[x1,y1...x70,y70]subN], [[z1,z2...z70]sub1...[z1..z70]subN]
        # Actually, as there will be two of each list above because there are two people en each video.
        face_2d, face_3d = get_face(p)
        hands_2d, hands_3d = get_hands(p)
        pose_2d, pose_3d = get_body(p)
        
        # Concatenates the coordinates for the face, hands and body on the last dimension, for each person.
        vid_input_p1, vid_input_p2 = ([fa+ha+po for fa, ha, po in zip(face_2d[i], hands_2d[i], pose_2d[i])] for i in range(2))
        vid_labels_p1, vid_labels_p2 = ([fa+ha+po for fa, ha, po in zip(face_3d[i], hands_3d[i], pose_3d[i])] for i in range(2))
        
        dataset.append(vid_input_p1)
        dataset.append(vid_input_p2)
        groundtruth.append(vid_labels_p1)
        groundtruth.append(vid_labels_p2)
        print(f'Completed folder {p}')
    return dataset, groundtruth

The following functions are in charge of retrieving the keypoints from each json. The json face json has a key *people* with a list of person objects. Each person object has *id* field and *landmarks* field, the latter containing a list of 3D coordinates for each keypoint.

In [4]:
def get_face(path):
    face_2D_seq = ([], [])
    face_3D_seq = ([], [])
    # List only the files (json), for there might be folders containing invalid frames.
    paths = map(lambda x: join(path, 'hdFace3d', x), sorted(listdir(join(path, 'hdFace3d'))))
    files = list(filter(lambda x: isfile(x), paths))
    for f in files[1:]: # The first frame of face keypoints estimation it's blank
        with open(f, 'r') as j:
            json_array = json.load(j)
            i = 0
            for person in json_array['people']:
                if person['id'] != -1: # If the id is -1, it means there's no person
                    x = person['face70']['landmarks'][::3]
                    y = person['face70']['landmarks'][1::3]
                    two_coord = [l[item] for item in range(len(x)) for l in [x,y]]
                    third_coord = person['face70']['landmarks'][2::3]
                    face_2D_seq[i].append(two_coord)
                    face_3D_seq[i].append(third_coord)
                    i+=1
            if i<2: # In case there was only one person detected on a frame
                face_2D_seq[i].append([0. for i in range(140)])
                face_3D_seq[i].append([0. for i in range(70)])
    print('Face completed.')
    # Each return var being a tuple with the list of n_frames list of coordinates for each person
    return face_2D_seq, face_3D_seq

The hands json contains the *landmarks* field inside both *left_hand* and *right_hand* field. As there are some frames that may not have one of the hands estimated, I've had to put some exception handling. 

In [5]:
def get_hands(path):
    hand_2D_seq = ([], [])
    hand_3D_seq = ([], [])
    paths = map(lambda x: join(path, 'hdHand3d', x), sorted(listdir(join(path, 'hdHand3d'))))
    files = list(filter(lambda x: isfile(x), paths))
    for f in files[1:-1]: # The first and the last frames of these folders are blank.
        with open(f, 'r') as j:
            json_array = json.load(j)
            i = 0
            for person in json_array['people']:
                if person['id'] != -1:
                    try:
                        # Separate x,y from z
                        hands= [[person[hand]['landmarks'][c] 
                                 for c in range(len(person['right_hand']['landmarks'])) if (c+1)%3!=0] 
                                 for hand in ['left_hand', 'right_hand']]
                        hand_2D_seq[i].append(hands[0]+hands[1])
                        
                        hands_3d = [person[hand]['landmarks'][2::3] 
                                    for hand in ['left_hand', 'right_hand']]
                        hand_3D_seq[i].append(hands_3d[0]+hands_3d[1])
                    
                    except Exception as e: # In case left_hand or right_hand keys don't exist.
                        if 'left_hand' in str(e): 
                            try: # Just put a 0., 0., 0. estimation for each keypoint of the left_hand
                                hands = [0. for i in range(42)]+[person['right_hand']['landmarks'][c] 
                                                                 for c in range(len(person['right_hand']['landmarks'])) if (c+1)%3!=0]
                                hands_3d = [0. for i in range(21)]+person['right_hand']['landmarks'][2::3]
                            except: # In case neither left_hand nor right_hand exist
                                hands = [0. for i in range(84)]
                                hands_3d = [0. for i in range(42)]
                        elif 'right_hand' in str(e): # Just put a 0., 0., 0. estimation for each keypoint of the right_hand
                            hands = [person['left_hand']['landmarks'][c] 
                                     for c in range(len(person['left_hand']['landmarks'])) if (c+1)%3!=0]+[0. for i in range(42)]
                            hands_3d = person['left_hand']['landmarks'][2::3]+[0. for i in range(21)]

                        hand_2D_seq[i].append(hands)
                        hand_3D_seq[i].append(hands_3d)
                    i+=1
            if i<2:
                hand_2D_seq[i].append([0. for i in range(84)])
                hand_3D_seq[i].append([0. for i in range(42)])
    print('Hands completed.')
    return hand_2D_seq, hand_3D_seq

The body json is organised a bit differently, inside each person object contains the *joints26* field with a list of 3D coordinates. But this list is structured as follows: *[x1,y1,z1,acc1,x2,y2,z2,acc2...]*.

In [6]:
def get_body(path):
    body_2D_seq = ([], [])
    body_3D_seq = ([], [])
    paths = map(lambda x: join(path, 'hdPose3d_stage1_op25', x), sorted(listdir(join(path, 'hdPose3d_stage1_op25'))))
    files = list(filter(lambda x: isfile(x), paths))
    for f in files[:-1]:
        with open(f, 'r') as j:
            json_array = json.load(j)
            i = 0
            for person in json_array['bodies']:
                if person['id'] != -1:
                    x = person['joints26'][::4]
                    y = person['joints26'][1::4]
                    two_coord = [l[item] for item in range(len(x)) for l in [x,y]]
                    third_coord = person['joints26'][2::4]
                    body_2D_seq[i].append(two_coord)
                    body_3D_seq[i].append(third_coord)
                    i += 1
            if i<2:
                body_2D_seq[i].append([0. for i in range(52)])
                body_3D_seq[i].append([0. for i in range(26)])
    print('Body completed.')
    return body_2D_seq, body_3D_seq

In [7]:
data_path = '../../../data/DB keypoints'
dataset, groundtruth = get_keypoints(data_path)

Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190419_asl2
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190419_asl4
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190419_asl5
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190425_asl1
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190425_asl2
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190425_asl3
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190425_asl5
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190425_asl7
Face completed.
Hands completed.
Body completed.
Completed folder ../../../data/DB keypoints/190425_asl9
Face completed.
Hands completed.
Body completed.
Comple

#### Load from pickle
Load keypoints from pre-saved pickle files instead of directly reading the jsons, can be found in below cells

## Dataset structuring
Now let's convert the lists obtained to Pytorch tensors and organise them in train, validation and test datasets. 
First, I will define a padding function in order to make all the sequences of video frames the same length, so I can train the LSTM in batches. 

In [8]:
def padding_seq(dataset):
    max_seq = max([len(x) for x in dataset])
    for seq in dataset:
        for i in range(max_seq-len(seq)):
            seq.append([np.nan for j in range(len(seq[0]))])
    return max_seq

max_seq = padding_seq(dataset)
padding_seq(groundtruth)

8751

In [9]:
# From python lists to numpy ndarray.
dataset = np.asarray(dataset)
groundtruth = np.asarray(groundtruth)
print(dataset.shape, groundtruth.shape)

(26, 8751, 276) (26, 8751, 138)


Once they are numpy ndarrays I save the keypoints into pickle files for faster loading in later executions

In [12]:
np.save('../pickles/dataset.npy', dataset)
np.save('../pickles/groundtruth.npy', groundtruth)

In [4]:
dataset = np.load('../../pickles/dataset.npy', allow_pickle=True)
groundtruth = np.load('../../pickles/groundtruth.npy', allow_pickle=True)
max_seq = dataset.shape[1]
print(max_seq)

8751


For each axis I normalize the keypoints using the following formula:

In [9]:
def norm_uniform(tensor, coordinates=1):
    max_value = [np.nanmax(tensor[:, :,i::coordinates]) for i in range(coordinates)]
    min_value = [np.nanmin(tensor[:, :,i::coordinates]) for i in range(coordinates)]
    center = [(max_value[i]+min_value[i])/2 for i in range(coordinates)]
    for j in range(coordinates):
        subtensor = tensor[:, :, j::coordinates]
        subtensor[:] = np.subtract(subtensor, center[j])
        subtensor[:] = np.divide(subtensor, max_value[j]-center[j])

norm_uniform(dataset,2)
norm_uniform(groundtruth)

In [10]:
def normalize(tensor, coordinates=1):
    mean_value = [np.nanmean(tensor[:, :,i::coordinates]) for i in range(coordinates)]
    std_value = [np.nanstd(tensor[:, :,i::coordinates]) for i in range(coordinates)]
    for j in range(coordinates):
        subtensor = tensor[:, :, j::coordinates]
        subtensor[:] = np.subtract(subtensor, mean_value[j])
        subtensor[:] = np.divide(subtensor, std_value[j])
  
    return [(mean_value[i], std_value[i]) for i in range(coordinates)]

mom_x, mom_y = normalize(dataset, 2)
print(mom_x, mom_y)
mz, stdz = normalize(groundtruth)[0]

(-0.0507053947525136, 0.29154502694827933) (-0.27880250002455587, 0.4229346271126893)


In [11]:
# From python lists to pytorch tensors.
dataset = torch.tensor(np.nan_to_num(dataset), dtype=torch.float32)
groundtruth = torch.tensor(np.nan_to_num(groundtruth), dtype=torch.float32)
print(dataset.shape, groundtruth.shape)

torch.Size([26, 8751, 276]) torch.Size([26, 8751, 138])


In [12]:
l1, l2 = len(dataset), len(groundtruth)
# Split in train, validation and test
training_kp, val_kp, test_kp = dataset[:round(0.70*l1)], dataset[round(0.70*l1):round(0.85*l1)], dataset[round(0.85*l1):]
training_lbl, val_lbl, test_lbl = groundtruth[:round(0.70*l2)], groundtruth[round(0.70*l2):round(0.85*l2)], groundtruth[round(0.85*l2):]
print(training_kp.shape, val_kp.shape, test_kp.shape)
print(training_lbl.shape, val_lbl.shape, test_lbl.shape)

torch.Size([18, 8751, 276]) torch.Size([4, 8751, 276]) torch.Size([4, 8751, 276])
torch.Size([18, 8751, 138]) torch.Size([4, 8751, 138]) torch.Size([4, 8751, 138])


Finally we define the batch_size and put the datasets in DataLoaders.

In [13]:
train_data = TensorDataset(training_kp, training_lbl)
val_data = TensorDataset(val_kp, val_lbl)
test_data = TensorDataset(test_kp, test_lbl)

batch_size = 2

train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size)
val_loader = DataLoader(val_data, shuffle=True, batch_size=batch_size)
test_loader = DataLoader(test_data, shuffle=True, batch_size=batch_size)

print(train_loader)

If we have a GPU available we set our device to GPU.

In [14]:
# torch.cuda.is_available() checks and returns a Boolean True if a GPU is available, else it'll return False
is_cuda = torch.cuda.is_available()

# If we have a GPU available, we'll set our device to GPU. We'll use this device variable later in our code.
if is_cuda:
    device = torch.device("cuda")
    print("GPU is available")
else:
    device = torch.device("cpu")
    print("GPU not available, CPU used")

GPU is available


Let's print some examples to see whether it is loaded correctly or not.

In [15]:
dataiter = iter(train_loader)
sample_x, sample_y = dataiter.next()

print(sample_x.shape, sample_y.shape)

torch.Size([2, 8751, 276]) torch.Size([2, 8751, 138])


## Model building
It is time to build the model for this approach. It will consist on a single/double layer LSTM followed by a Linear layer with output size the number of keypoints we want to estimate. I also define a method to initialize the hidden_state of the cell.

In [16]:
class LSTM_2D3D(nn.Module):
    
    def __init__(self, input_size, output_size, hidden_dim, n_layers, bidirectional, dropout=0.):
        super().__init__()
        # Save the model parameters
        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim
        self.bi = bidirectional
        
        # Define the architecture
        self.lstm = nn.LSTM(input_size, hidden_dim, n_layers, batch_first=True, bidirectional=bidirectional)
        self.fc = nn.Sequential(
            nn.Linear(hidden_dim*(2 if self.bi else 1), output_size),
            nn.ReLU()
        )
        
    def forward(self, x, state):
        # Describe the forward step
        batch_size, seq_len = x.size(0), x.size(1) # We save the batch size and the sequence length
        ht, hidden_state = self.lstm(x, state)
        ht = ht.contiguous().view(-1, self.hidden_dim*(2 if self.bi else 1)) # Need to flatten and reshape the output to feed it to the Linear layer
        ot = self.fc(ht)
        ot = ot.view(batch_size, seq_len, -1) # Reshape the output for it to be torch.Size([batch_size, seq_len, output_size])
        return ot, hidden_state
    
    def init_hidden(self, batch_size):
        weight = next(self.parameters()).data
        hidden = (weight.new(self.n_layers*(2 if self.bi else 1), batch_size, self.hidden_dim).zero_().to(device),
                      weight.new(self.n_layers*(2 if self.bi else 1), batch_size, self.hidden_dim).zero_().to(device))
        return hidden

In [30]:
# Define some model parameters
INPUT_SIZE = sample_x.size(2)
OUTPUT_SIZE = sample_y.size(2)
HIDDEN_DIM = 1024
N_LAYERS = 2
BIDIRECTIONAL = True

# Instantiate the model
model = LSTM_2D3D(INPUT_SIZE, OUTPUT_SIZE, HIDDEN_DIM, N_LAYERS, BIDIRECTIONAL)
model.to(device)
print(model)

LSTM_2D3D(
  (lstm): LSTM(276, 1024, num_layers=2, batch_first=True, bidirectional=True)
  (fc): Sequential(
    (0): Linear(in_features=2048, out_features=138, bias=True)
    (1): ReLU()
  )
)


## Training
Now we will proceed with the training. The first cell will define the learning rate, the loss function and the selected optimizer for the training process. Then we will proceed with a training over a number of epochs in which we will print it's training loss and validation loss. I also will be using Tensorboard to have a much nicer view of the results.

In [31]:
def substract_root_PJPE(output):
    jf = torch.chunk(output[:, :, :70], max_seq, dim=1)
    jhl, jhr = torch.chunk(output[:, :, 70:91], max_seq, dim=1), torch.chunk(output[:, :, 91:112], max_seq, dim=1)
    jb = torch.chunk(output[:, :, 112:], max_seq, dim=1)
    joints_merged = []
    roots = [33, 0, 0, 8]
    for i, joints in enumerate((jf, jhl, jhr, jb)):
        n_joints = []
        for chunk in joints:
            n_joints.append(chunk.sub(chunk[:,:,roots[i]].unsqueeze(2)))
        joints_merged.append(torch.cat(tuple(n_joints), dim=1))
    joints_merged = torch.cat(tuple(joints_merged), dim=2)
    return joints_merged

In [32]:
NUM_EPOCHS = 35
lr = 1.5e-3
loss_function = nn.MSELoss()
one_cycle = True
optimizer = optim.Adam(model.parameters(), lr=lr)
if one_cycle:
    scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, max_lr=lr, 
                                                  steps_per_epoch=len(train_loader), epochs=NUM_EPOCHS,
                                                  div_factor=18.0, final_div_factor=800.0)

In [33]:
from datetime import datetime
name = 'lot_whole'
writer = SummaryWriter(log_dir=f'/deeplearning/logs/{name}{datetime.now()}_lr-{lr}')

In [36]:
timer_beg = timer()

tr_losses = []
val_losses = []

model.train()
for i in range(NUM_EPOCHS):
    # Init the hidden state (ht, ct)
    h = model.init_hidden(batch_size)
    batch_losses = []
    train_MPJPE = []
    
    if i+1 == NUM_EPOCHS:
        preds, inps, labls = [], [], []
        val_preds, val_inps, val_labls = [], [], []
    
    for inputs, labels in train_loader:
        h = tuple([e.data for e in h])
        inputs, labels = inputs.to(device), labels.to(device)
        # Clear the gradients
        optimizer.zero_grad()
        # Forward step
        output, h = model(inputs, h)
        
        if i+1 == NUM_EPOCHS:
            preds.append(output)
            inps.append(inputs)
            labls.append(labels)
        
        # Loss calculation and backward step
        loss = loss_function(output, labels.float())
        loss.backward()
        # Weight update
        optimizer.step()
        # One cycle policy step
        if one_cycle:
            scheduler.step()
        
        # Output data collection for showing
        batch_losses.append(loss.item())
        rooted_o, rooted_l = substract_root_PJPE(output), substract_root_PJPE(labels)
        train_MPJPE.append(rooted_o.sub(rooted_l).abs().mean().item())
    
    if i+1 == NUM_EPOCHS: # Save predictions
        tr_predictions = torch.cat(tuple(preds), dim=0)
        tr_inputs = torch.cat(tuple(inps), dim=0)
        tr_groundtruth = torch.cat(tuple(labls), dim=0)
    
    timer_end = timer()
    tr_losses.append(np.mean(batch_losses))
    writer.add_scalar('Loss/train', tr_losses[-1], i)   
    train_MPJPE_total = np.mean(train_MPJPE)
    
    # Validation at the end of an epoch
    val_h = model.init_hidden(batch_size)
    model.eval()
    val_loss = []
    val_MPJPE = []
    
    for inp, lab in val_loader:
        val_h = tuple([each.data for each in val_h])
        inp, lab = inp.to(device), lab.to(device)
        out, val_h = model(inp, val_h)
        
        if i+1 == NUM_EPOCHS:
            val_preds.append(output)
            val_inps.append(inp)
            val_labls.append(lab)
        
        val_loss.append(loss_function(out, lab.float()).item())
        rooted_o, rooted_l = substract_root_PJPE(out), substract_root_PJPE(lab)
        val_MPJPE.append(rooted_o.sub(rooted_l).abs().mean().item())
    
    if i+1 == NUM_EPOCHS: # Save predictions
        val_predictions = torch.cat(tuple(val_preds), dim=0)
        val_inputs = torch.cat(tuple(val_inps), dim=0)
        val_groundtruth = torch.cat(tuple(val_labls), dim=0)
    
    val_losses.append(np.mean(val_loss))
    writer.add_scalar('Loss/validation', val_losses[-1], i)  
    val_MPJPE_total = np.mean(val_MPJPE)
    model.train()
    
    # Output loss and training time.
    print(f"Finished epoch {i+1}/{NUM_EPOCHS} in {(timer_end-timer_beg):.2f}s.\n",
             f"Loss: {np.mean(tr_losses[-1]):.4f}",
             f" Val Loss: {val_losses[-1]:.4f}\n"
             f"Train MPJPE: {train_MPJPE_total*stdz:.4f}", f" Val MPJPE: {val_MPJPE_total*stdz:.4f}")
    timer_beg = timer()

plt.figure()
plt.plot(tr_losses, label='train')
plt.plot(val_losses, label='validation')
plt.xlabel('Epoch')
plt.ylabel('MSELoss')
plt.legend()

RuntimeError: CUDA out of memory. Tried to allocate 684.00 MiB (GPU 0; 2.95 GiB total capacity; 1.50 GiB already allocated; 53.62 MiB free; 2.11 GiB reserved in total by PyTorch)

In [23]:
zeros = torch.zeros((138), device='cuda:0')

for i in range(len(tr_predictions)):
    count=0
    for frame in tr_predictions[i]:
        if torch.all(frame.eq(zeros)):
            count +=1
    print(count, end=' ')
    count=0
    for frame in tr_groundtruth[i]:
        if torch.all(frame.eq(zeros)):
            count +=1
    print(f'vs. {count}')

0 vs. 0
8626 vs. 1798
414 vs. 479
8747 vs. 479
507 vs. 0
425 vs. 479
8445 vs. 0
1739 vs. 1798
1845 vs. 1798
8554 vs. 480
8255 vs. 1140
8442 vs. 174
8692 vs. 2906
447 vs. 480
8714 vs. 479
2847 vs. 2906
8313 vs. 2739
144 vs. 0


In [23]:
print(stdz)

0.39241344730563404


In [24]:
torch.save(model.state_dict(), f'./{name}.pt')

In [25]:
model.load_state_dict(torch.load(f'./{name}.pt'))

<All keys matched successfully>

## Testing
After the training, we shall proceed with the performance test. This will go through the test batches and perform the inference, then it will show the test loss, as well as the performance metric. In this case, as we are working with human body keypoints, we will use the Mean Per Joint Position Error (MPJPE) metric, which outputs the mean euclidean distance between the joints (keypoints) positions estimated and the ones in the groundtruth.

The formula for MPJPE is the following:

$\text{MPJPE} = \frac1T\frac1N\displaystyle\sum_{t=1}^{T}\displaystyle\sum_{i=1}^{N}\|(J_{i}^{(t)}-J_{root}^{(t)})-(Ĵ_{i}^{(t)}-Ĵ_{root}^{(t)})\|$

Where N is the number of joints, and T the number of samples.

As we have seen in the formula above, we need to align the root joints of the labels and the network output. In order to do that, I have defined a function (`substract_root_PJPE`) that substracts the root joint of each keypoint set (face, hands, body) in the corresponding keypoint set.

In [26]:
test_losses = []
MPJPE = []
h = model.init_hidden(batch_size)
preds, inps, labls = [], [], []

model.eval()
for inputs_test, labels_test in test_loader:
    
    h = tuple([each.data for each in h])
    inputs_test, labels_test = inputs_test.to(device), labels_test.to(device)
    
    output_test, h = model(inputs_test, h)
    preds.append(output_test)
    inps.append(inputs_test)
    labls.append(labels_test)
    
    test_loss = loss_function(output_test, labels_test.float())
    test_losses.append(test_loss.item())
    rooted_o, rooted_l = substract_root_PJPE(output_test), substract_root_PJPE(labels_test)
    MPJPE.append(rooted_o.sub(rooted_l).abs().mean().item())

test_predictions = torch.cat(tuple(preds), dim=0)
test_inputs = torch.cat(tuple(inps), dim=0)
test_groundtruth = torch.cat(tuple(labls), dim=0)
MPJPE_total = np.mean(MPJPE)

In [27]:
print(f"MPJPE: {MPJPE_total*stdz:.4f}", f"\nTest loss: {np.mean(test_losses):.4f}")

MPJPE: 0.0213 
Test loss: 0.5268


### Save the results into a json

## Interpreation

Now to better understanding of the results, I will plot some of the frames from the last batches on the training and validation, and also from testing.

In [28]:
def plot_and_rotate(c_inputs, c_z, frames, frame):
    c_inputs[:,::2].mul_(mom_x[1])
    c_inputs[:,1::2].mul_(mom_y[1])
    c_z.mul_(stdz)

    bodiesXY = torch.chunk(c_inputs[frames, :], len(frames), dim=0)
    bodiesZ = torch.chunk(c_z[frames, :], len(frames), dim=0)
    
    x = bodiesXY[frame].squeeze()[::2]
    y = bodiesXY[frame].squeeze()[1::2]
    z = bodiesZ[frame].squeeze()

    r_eyebrow = [[c[i] for i in range(17, 22)] for c in [x,y,z]]
    l_eyebrow = [[c[i] for i in range(22, 27)] for c in [x,y,z]]
    l_eye = [[c[i] for i in range(42, 48)] for c in [x,y,z]]
    r_eye = [[c[i] for i in range(36, 42)] for c in [x,y,z]]
    nose1 = [[c[i] for i in range(27, 31)] for c in [x,y,z]]
    nose2 = [[c[i] for i in range(31, 36)] for c in [x,y,z]]
    ext_mouth = [[c[i] for i in range(48, 60)] for c in [x,y,z]]
    int_mouth = [[c[i] for i in range(60, 68)] for c in [x,y,z]]
    contour = [[c[i] for i in range(0, 17)] for c in [x,y,z]]
    
    l_arm = [[c[i+112] for i in [1, 0, 9, 10, 11]] for c in [x,y,z]]
    r_arm = [[c[i+112] for i in [0, 3, 4, 5]] for c in [x,y,z]]
    l_leg = [[c[i+112] for i in [0, 2, 12, 13, 14, 22, 23, 24]] for c in [x,y,z]]
    r_leg = [[c[i+112] for i in [2, 6, 7, 8, 19, 20, 21]] for c in [x,y,z]]
    head = [[c[i+112] for i in [18, 17, 1, 15, 16]] for c in [x,y,z]]

    rh0 = [[c[i+70] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]]
    rh1 = [[c[i+70] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]]
    rh2 = [[c[i+70] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]]
    rh3 = [[c[i+70] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]]
    rh4 = [[c[i+70] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]]
    lh0 = [[c[i+91] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]]
    lh1 = [[c[i+91] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]]
    lh2 = [[c[i+91] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]]
    lh3 = [[c[i+91] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]]
    lh4 = [[c[i+91] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]]
    
    fig = plt.figure()
    ax = fig.add_subplot(111, projection='3d')
    def init():
        ax.plot(r_eyebrow[0], r_eyebrow[2], r_eyebrow[1])
        ax.plot(l_eyebrow[0], l_eyebrow[2], l_eyebrow[1])
        ax.plot(l_eye[0], l_eye[2], l_eye[1])
        ax.plot(r_eye[0], r_eye[2], r_eye[1])
        ax.plot(nose1[0], nose1[2], nose1[1])
        ax.plot(nose2[0], nose2[2], nose2[1])
        ax.plot(ext_mouth[0], ext_mouth[2], ext_mouth[1])
        ax.plot(int_mouth[0], int_mouth[2], int_mouth[1])
        
        ax.plot(rh0[0], rh0[2], rh0[1])
        ax.plot(rh1[0], rh1[2], rh1[1])
        ax.plot(rh2[0], rh2[2], rh2[1])
        ax.plot(rh3[0], rh3[2], rh3[1])
        ax.plot(rh4[0], rh4[2], rh4[1])
        
        ax.plot(lh0[0], lh0[2], lh0[1])
        ax.plot(lh1[0], lh1[2], lh1[1])
        ax.plot(lh2[0], lh2[2], lh2[1])
        ax.plot(lh3[0], lh3[2], lh3[1])
        ax.plot(lh4[0], lh4[2], lh4[1])
        
        ax.plot(r_arm[0], r_arm[2], r_arm[1])
        ax.plot(l_arm[0], l_arm[2], l_arm[1])
        ax.plot(r_leg[0], r_leg[2], r_leg[1])
        ax.plot(l_leg[0], l_leg[2], l_leg[1])
        ax.plot(head[0], head[2], head[1])
        ax.set_xlim(-1,1)
        ax.set_ylim(-1,1)
        ax.set_zlim(-1,1)

        return fig,

    def animate(i):
        ax.view_init(elev=220., azim=3.6*i)
        return fig,

    # Animate
    ani = animation.FuncAnimation(fig, animate, init_func=init,
                               frames=100, interval=100, blit=True)    

    return ani

In [44]:
def plot_frames(predictions, groundtruth, inputs, video_n, frames):
    
    inp = inputs.clone()
    preds = predictions.clone()
    grtr = groundtruth.clone()
    
    inp[:,:,::2].mul_(mom_x[1])
    inp[:,:,1::2].mul_(mom_y[1])
    preds.mul_(stdz)
    grtr.mul_(stdz)
    
    bodiesXY = torch.chunk(inp[video_n, frames, :], len(frames), dim=0)
    pred_bodiesZ = torch.chunk(preds[video_n, frames, :], len(frames), dim=0)
    true_bodiesZ = torch.chunk(grtr[video_n, frames, :], len(frames), dim=0)
   
    nrows = np.ceil(len(frames)/2)
    fig = plt.figure(figsize=(15, 6*nrows))
    fig2 = plt.figure(figsize=(15, 6*nrows))
    for frame in range(len(frames)):
        x = bodiesXY[frame].squeeze()[::2]
        y = bodiesXY[frame].squeeze()[1::2]
        pred_z = pred_bodiesZ[frame].squeeze()
        true_z = true_bodiesZ[frame].squeeze()
        
        r_eyebrow = tuple([[c[i] for i in range(17, 22)] for c in [x,y,z]] for z in [pred_z, true_z])
        l_eyebrow = tuple([[c[i] for i in range(22, 27)] for c in [x,y,z]] for z in [pred_z, true_z])
        l_eye = tuple([[c[i] for i in range(42, 48)] for c in [x,y,z]] for z in [pred_z, true_z])
        r_eye = tuple([[c[i] for i in range(36, 42)] for c in [x,y,z]] for z in [pred_z, true_z])
        nose1 = tuple([[c[i] for i in range(27, 31)] for c in [x,y,z]] for z in [pred_z, true_z])
        nose2 = tuple([[c[i] for i in range(31, 36)] for c in [x,y,z]] for z in [pred_z, true_z])
        ext_mouth = tuple([[c[i] for i in range(48, 60)] for c in [x,y,z]] for z in [pred_z, true_z])
        int_mouth = tuple([[c[i] for i in range(60, 68)] for c in [x,y,z]] for z in [pred_z, true_z])
        contour = tuple([[c[i] for i in range(0, 17)] for c in [x,y,z]] for z in [pred_z, true_z])
        
        rh0 = tuple([[c[i+70] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh1 = tuple([[c[i+70] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh2 = tuple([[c[i+70] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh3 = tuple([[c[i+70] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh4 = tuple([[c[i+70] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh0 = tuple([[c[i+91] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh1 = tuple([[c[i+91] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh2 = tuple([[c[i+91] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh3 = tuple([[c[i+91] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh4 = tuple([[c[i+91] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]] for z in [pred_z, true_z])
        
        l_arm = tuple([[c[i+112] for i in [1, 0, 9, 10, 11]] for c in [x,y,z]] for z in [pred_z, true_z])
        r_arm = tuple([[c[i+112] for i in [0, 3, 4, 5]] for c in [x,y,z]] for z in [pred_z, true_z])
        l_leg = tuple([[c[i+112] for i in [0, 2, 12, 13, 14, 22, 23, 24]] for c in [x,y,z]] for z in [pred_z, true_z])
        r_leg = tuple([[c[i+112] for i in [2, 6, 7, 8, 19, 20, 21]] for c in [x,y,z]] for z in [pred_z, true_z])
        head = tuple([[c[i+112] for i in [18, 17, 1, 15, 16]] for c in [x,y,z]] for z in [pred_z, true_z])

        ax = fig.add_subplot(nrows, 2, frame+1, projection='3d')
        ax.plot(r_eyebrow[0][0], r_eyebrow[0][2], r_eyebrow[0][1])
        ax.plot(l_eyebrow[0][0], l_eyebrow[0][2], l_eyebrow[0][1])
        ax.plot(l_eye[0][0], l_eye[0][2], l_eye[0][1])
        ax.plot(r_eye[0][0], r_eye[0][2], r_eye[0][1])
        ax.plot(nose1[0][0], nose1[0][2], nose1[0][1])
        ax.plot(nose2[0][0], nose2[0][2], nose2[0][1])
        ax.plot(ext_mouth[0][0], ext_mouth[0][2], ext_mouth[0][1])
        ax.plot(int_mouth[0][0], int_mouth[0][2], int_mouth[0][1])
        
        ax.plot(rh0[0][0], rh0[0][2], rh0[0][1])
        ax.plot(rh1[0][0], rh1[0][2], rh1[0][1])
        ax.plot(rh2[0][0], rh2[0][2], rh2[0][1])
        ax.plot(rh3[0][0], rh3[0][2], rh3[0][1])
        ax.plot(rh4[0][0], rh4[0][2], rh4[0][1])
        
        ax.plot(lh0[0][0], lh0[0][2], lh0[0][1])
        ax.plot(lh1[0][0], lh1[0][2], lh1[0][1])
        ax.plot(lh2[0][0], lh2[0][2], lh2[0][1])
        ax.plot(lh3[0][0], lh3[0][2], lh3[0][1])
        ax.plot(lh4[0][0], lh4[0][2], lh4[0][1])
        
        ax.plot(r_arm[0][0], r_arm[0][2], r_arm[0][1])
        ax.plot(l_arm[0][0], l_arm[0][2], l_arm[0][1])
        ax.plot(r_leg[0][0], r_leg[0][2], r_leg[0][1])
        ax.plot(l_leg[0][0], l_leg[0][2], l_leg[0][1])
        ax.plot(head[0][0], head[0][2], head[0][1])
        
        ax2 = fig2.add_subplot(nrows, 2, frame+1, projection='3d')
        ax2.plot(r_eyebrow[1][0], r_eyebrow[1][2], r_eyebrow[1][1])
        ax2.plot(l_eyebrow[1][0], l_eyebrow[1][2], l_eyebrow[1][1])
        ax2.plot(l_eye[1][0], l_eye[1][2], l_eye[1][1])
        ax2.plot(r_eye[1][0], r_eye[1][2], r_eye[1][1])
        ax2.plot(nose1[1][0], nose1[1][2], nose1[1][1])
        ax2.plot(nose2[1][0], nose2[1][2], nose2[1][1])
        ax2.plot(ext_mouth[1][0], ext_mouth[1][2], ext_mouth[1][1])
        ax2.plot(int_mouth[1][0], int_mouth[1][2], int_mouth[1][1])
        
        ax2.plot(rh0[1][0], rh0[1][2], rh0[1][1])
        ax2.plot(rh1[1][0], rh1[1][2], rh1[1][1])
        ax2.plot(rh2[1][0], rh2[1][2], rh2[1][1])
        ax2.plot(rh3[1][0], rh3[1][2], rh3[1][1])
        ax2.plot(rh4[1][0], rh4[1][2], rh4[1][1])
        
        ax2.plot(lh0[1][0], lh0[1][2], lh0[1][1])
        ax2.plot(lh1[1][0], lh1[1][2], lh1[1][1])
        ax2.plot(lh2[1][0], lh2[1][2], lh2[1][1])
        ax2.plot(lh3[1][0], lh3[1][2], lh3[1][1])
        ax2.plot(lh4[1][0], lh4[1][2], lh4[1][1])
        
        ax2.plot(r_arm[1][0], r_arm[1][2], r_arm[1][1])
        ax2.plot(l_arm[1][0], l_arm[1][2], l_arm[1][1])
        ax2.plot(r_leg[1][0], r_leg[1][2], r_leg[1][1])
        ax2.plot(l_leg[1][0], l_leg[1][2], l_leg[1][1])
        ax2.plot(head[1][0], head[1][2], head[1][1])
        
        ax.set_xlim(-1,1)
        ax.set_ylim(-1,1)
        ax.set_zlim(-1,1)
        ax2.set_xlim(-1,1)
        ax2.set_ylim(-1,1)
        ax2.set_zlim(-1,1)

        ax.view_init(elev=220., azim=185.)
        ax2.view_init(elev=220., azim=185.)


### Single frame
On the first cell you can select which frames you want to plot and from which video of the batch. On the second you select which frame of the previosly selected you want to plot, specifying its index on the declared "frames" list.

In [40]:
# Last batches of training -output, inputs, labels-.
vid = 6
frames = [1, 3000, 6500]

c_inputs = tr_inputs[vid].clone()
c_output = tr_predictions[vid].clone()
c_labels = tr_groundtruth[vid].clone()

In [41]:
HTML(plot_and_rotate(c_inputs, c_output, frames, 1).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [32]:
c_inputs = tr_inputs[vid].clone()
HTML(plot_and_rotate(c_inputs, c_labels, frames, 1).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

We repeat the same process for the last test batch.

In [33]:
# Last batches of test -output_test, inputs_test, labels_test-.
vid = 3
frames = [200, 3000]

c_inputs = test_inputs[vid].clone()
c_output = test_predictions[vid].clone()
c_labels = test_groundtruth[vid].clone()

In [34]:
HTML(plot_and_rotate(c_inputs, c_output, frames, 0).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [35]:
c_inputs = test_inputs[vid].clone()
HTML(plot_and_rotate(c_inputs, c_labels, frames, 0).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

### Slice of frames
Now let's plot a sequence of frames of the selected video. We will plot both the groundtruth and the predicted.

In [45]:
frames = [i for i in range(100,110)]
video_n = 6

In [46]:
plot_frames(tr_predictions, tr_groundtruth, tr_inputs, video_n, frames)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …